In [1]:
!pip install google_colab_selenium pandas -q

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.5/9.5 MB 23.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 467.7/467.7 kB 14.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 58.3/58.3 kB 3.5 MB/s eta 0:00:00


In [86]:
import json
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
import google_colab_selenium as gs

driver = gs.ChromeDriver()

<IPython.core.display.Javascript object>

In [92]:
def scrape_categories(url):
    category = url.split('#')[0].split('/')[-1]
    items = []
    # Send a GET request to the website
    try:
        driver.get(url)
        WebDriverWait(driver, 50).until(EC.presence_of_all_elements_located((By.TAG_NAME, "tx-video-card")))
        # Find all <tx-video-card> elements
        card_elements = driver.find_elements(By.TAG_NAME, "tx-video-card")
        for card in card_elements:
          url = card.find_element(By.TAG_NAME, 'a').get_attribute('href')
          title = card.find_element(By.TAG_NAME, 'h3').text
          items.append({"url": url, "title": title, "category": category})

    except Exception as e:
        print("An error occurred:", e)
    return items

In [93]:
def scrape_article(item):
    # Send a GET request to the website
    try:
        driver.get(item['url'])
        item['text'] = []
        WebDriverWait(driver, 50).until(EC.presence_of_all_elements_located((By.TAG_NAME, "p")))

        # Find all <p> elements and filter empty elements
        p_elements = driver.find_elements(By.TAG_NAME, "p")
        p_elements = list(filter(lambda p: p.text, p_elements))

        # Print the text of each <p> element
        for p in p_elements:
          if p.text.strip().startswith('ZDF'):
            item['attribution'] = p.text.strip()
            continue
          if p.text.strip().startswith('http'):
            item['source'] = p.text.strip()

          item['text'].append(p.text)

    except Exception as e:
        print("An error occurred:", e)
    return item

In [ ]:
urls = [
    'https://terraxplaincommons.zdf.de/kategorie/geowissenschaften#videos',
    'https://terraxplaincommons.zdf.de/kategorie/der-menschliche-koerper#videos',
    'https://terraxplaincommons.zdf.de/kategorie/Biologie#videos',
    'https://terraxplaincommons.zdf.de/kategorie/Geschichte#videos',
    'https://terraxplaincommons.zdf.de/kategorie/religion#videos',
    'https://terraxplaincommons.zdf.de/kategorie/physik#videos',
    'https://terraxplaincommons.zdf.de/kategorie/technik#videos',
    'https://terraxplaincommons.zdf.de/kategorie/chemie#videos',
    'https://terraxplaincommons.zdf.de/kategorie/mathematik#videos',
    'https://terraxplaincommons.zdf.de/kategorie/sozialkunde#videos',
    'https://terraxplaincommons.zdf.de/kategorie/klima-und-klimawandel#videos',
    'https://terraxplaincommons.zdf.de/kategorie/unesco-welterbestaetten#videos'
]

for url in urls:
  items = scrape_categories(url)
  items = map(scrape_article, items)
  with open('data.jsonl', 'a') as f:
    for item in items:
      f.write(json.dumps(item) + '\n')

driver.quit()

In [233]:
import pandas as pd

df = pd.read_json('data.jsonl', lines=True)

In [234]:
print(len(df))
# Filter rows where 'url' is null
df = df[df['url'].notnull()]
# Filter rows where 'attribution' is null
df = df[df['attribution'].notnull()]
print(len(df))

400
331


In [235]:
df['text'] = df['text'].apply(lambda arr: [s for s in arr if 'Mehr von Terra X' not in s])
df['text'] = df['text'].apply(lambda arr: [s for s in arr if 'https:' not in s])
df['text'] = df['text'].apply(lambda arr: [s for s in arr if len(s) >= 20])

In [236]:
# Filter rows with text array length 0
df = df[df['text'].apply(len) > 0]
print(len(df))

331


In [237]:
# Filter rows with text array length < 3
df = df[df['text'].apply(len) < 3]
print(len(df))

283


In [238]:
# Create new column 'short_text' containing the shorter string from each array
df['short_text'] = df['text'].apply(lambda arr: min(arr, key=len))

# Delete the 'short_text' from the 'text' array
df['text'] = df['text'].apply(lambda arr: max(arr, key=len))

# Convert the 'text' array to a string
df['text'] = df['text'].str.join('')

In [239]:
df['source'] = df['source'].fillna('')

In [ ]:
print(df.head())

In [241]:
df.to_json('clean_data.jsonl', orient='records', lines=True)